In [1]:
from astropy.io import fits
from astropy.coordinates import SkyCoord, match_coordinates_sky
from astropy import units as u
import numpy as np
import matplotlib.pyplot as plt
from pathlib import Path
import healpy as hp
import math

In [2]:
hsc_dir_name = '/data/des90.a/data/jsanch87/HSC/PDR2/'
hsc_files = ['HSC_i_lt_22.fits',\
             'HSC_22_i_22p5.fits',\
             'HSC_23p5_i_24p5.fits',\
             'HSC_24p5_i_25.fits']

delve_dir_name = '/data/des91.b/data/kadrlica/projects/delve/cat/y2t1/r1/cat/'
delve_base_file_name = 'cat_hpx_0'
delve_ext = '.fits'

In [3]:
bright_mag = 27
dim_mag = 1
brightest = 27
dimmest = 1
lower_spread_limit = -0.025
upper_spread_limit = 0.045
min_ext = 0.003
wide_ext = 0.005
max_sep = 0.5 * u.arcsec
debug = False
nSides = 32
channel = 'i'

In [4]:
def set_mag_limits(data, bright, dim):
  true_mags = data[np.isnan(data[f'{channel}_cmodel_mag']) == False]
  good_mags = true_mags[true_mags[f'{channel}_cmodel_mag'] < 35]
  if np.min(good_mags[f'{channel}_cmodel_mag']) < bright:
    upper = np.min(good_mags[f'{channel}_cmodel_mag'])
  if np.max(good_mags[f'{channel}_cmodel_mag']) > dim:
    lower = np.max(good_mags[f'{channel}_cmodel_mag'])

  return upper, lower

In [5]:
def calc_matches(delve_ds, hsc_ds):
  if (len(delve_ds) > 0) & (len(hsc_ds) > 0):
    delve_sky = SkyCoord(ra=delve_ds['ra']*u.degree,dec=delve_ds['dec']*u.degree)    
    hsc_sky = SkyCoord(ra=hsc_ds['ra']*u.degree,dec=hsc_ds['dec']*u.degree)
    idx, d2d, d3d = match_coordinates_sky(delve_sky, hsc_sky)
    sep_constraint = d2d < max_sep
    delve_matches = delve_ds[sep_constraint]
    fraction = len(delve_matches) / len(delve_ds)
  else:
    delve_matches = []
    fraction = 0.0
  if debug == True:
    print(f'Fraction of delve galaxies that are also in {hsc_file_name} at pixel {pixel}: {fraction}')
  return delve_matches

In [6]:
# Set up dictionaries for storing data
match = []
full = []
hsc_pixel_coverage = {}
hsc_pixel_coverage['dec'] = []
hsc_pixel_coverage['ra'] = []
hsc_pixel_coverage['extent'] = []
delve_pixel_coverage = {}
delve_pixel_coverage['dec'] = []
delve_pixel_coverage['ra'] = []
delve_pixel_coverage['extent'] = []
  
for hsc_file_name in hsc_files:
  hsc_fqpn = hsc_dir_name + hsc_file_name
  hsc_hdul = fits.open(hsc_fqpn, memmap=True)

  hsc_data = hsc_hdul[1].data
  if debug == True:
    print ('Initial hsc data size: ', len(hsc_data))

  # Determine pixel for each HSC object
  hsc_pixel = hp.ang2pix(nSides,hsc_data['ra'],hsc_data['dec'],lonlat=True)
  pixel_list = np.unique(hsc_pixel)

  # Look at HSC objects on a pixel by pixel basis
  for pixel in pixel_list:

    # Check that the HSC pixel has valid data in it for the channel in question
    indices = (hsc_pixel == pixel)
    hsc_pix_objs = hsc_data[indices]

    mag_test = hsc_pix_objs[hsc_pix_objs[f'{channel}_cmodel_mag'] != 0.0]
    if len(mag_test) == 0:
      continue

    mag_test = mag_test[np.isnan(mag_test[f'{channel}_cmodel_mag']) == False]
    if len(mag_test) == 0:
      continue

    # Get magnitude range for HSC pixel
    bright_mag = 27
    dim_mag = 1
    bright_mag, dim_mag = set_mag_limits(hsc_pix_objs,bright_mag,dim_mag)

    # Look for equivalent Delve pixel
    delve_fqpn = delve_dir_name + delve_base_file_name + str(pixel) + delve_ext
    delve_check = Path(delve_fqpn)
    if delve_check.is_file():
    
      # Subdivide pixel into 16 pieces to get subpixel coverage by HSC
      subpixels = hp.ang2pix(nSides*4,hsc_pix_objs['ra'],hsc_pix_objs['dec'],lonlat=True)
      subpixel_list = np.unique(subpixels)
      occupancy = len(subpixel_list) / 16
      pix_ra, pix_dec = hp.pix2ang(nSides,pixel,lonlat=True)
      if debug == True:
        print('HSC pixel center: ',pix_ra,pix_dec)
      hsc_pixel_coverage['dec'].append(pix_dec)
      hsc_pixel_coverage['ra'].append(pix_ra)
      hsc_pixel_coverage['extent'].append(occupancy)

      # Open Delve file and get data
      delve_hdul = fits.open(delve_fqpn, memmap=True)
      delve_data = delve_hdul[1].data
      if debug == True:
        print('Initial delve data size: ', len(delve_data))

      # Subdivide pixel into 16 pieces to get subpixel coverage by Delve
      subpixels = hp.ang2pix(nSides*4,delve_data['ra'],delve_data['dec'],lonlat=True)
      subpixel_list = np.unique(subpixels)
      occupancy = len(subpixel_list) / 16
      pix_ra, pix_dec = hp.pix2ang(nSides,pixel,lonlat=True)
      if debug == True:
        print('Delve pixel center: ',pix_ra, pix_dec)
      delve_pixel_coverage['dec'].append(pix_dec)
      delve_pixel_coverage['ra'].append(pix_ra)
      delve_pixel_coverage['extent'].append(occupancy)

      # Eliminate Delve objects outside of magnitude range
      indices = (delve_data[f'mag_auto_{channel}'] > bright_mag) & (delve_data[f'mag_auto_{channel}'] < dim_mag)
      delve_pix_objs = delve_data[indices]

      if (len(hsc_pix_objs) > 0) & (len(delve_pix_objs) > 0):
        # Find Delve objects in HSC catalog and load it into the running array
        delve_hsc = calc_matches(delve_pix_objs,hsc_pix_objs)
        if debug == True:
          print('Number of matched objects: ', len(delve_hsc))
        if len(delve_hsc) > 0:
          if len(match) == 0:
            match = delve_hsc[f'mag_auto_{channel}']
          else:
            match = np.concatenate((match,delve_hsc[f'mag_auto_{channel}']))
        if len(full) == 0:
          full = delve_pix_objs[f'mag_auto_{channel}']
        else:
          full = np.concatenate((full,delve_pix_objs[f'mag_auto_{channel}']))
        if bright_mag < brightest:
          brightest = bright_mag
        if dim_mag > dimmest:
          dimmest = dim_mag
      delve_hdul.close()
  hsc_hdul.close()

FileNotFoundError: [Errno 2] No such file or directory: 'data/des90.a/data/jsanch87/HSC/PDR2/HSC_i_lt_22.fits'

In [ ]:
# plot ratio of Delve objects found in HSC database
low_range = math.floor(brightest - 1.0)
high_range = math.ceil(dimmest + 1.0)
hist_match, bin_edges_match = np.histogram(match,range=(low_range,high_range),bins=high_range-low_range)
hist_full, bin_edges_full = np.histogram(full,range=(low_range,high_range),bins=high_range-low_range)
ratio = 1.0 * hist_match / hist_full
bin_centers = 0.5 * bin_edges_match[1:] + 0.5 * bin_edges_match[:-1]
plt.plot(bin_centers,ratio)

# plot pixel coverage for HSC and Delve data
fig, (ax1, ax2) = plt.subplots(2,1,figsize=(15,7))
fig.suptitle('Pixel coverage for HSC and Delve data')

ax1.scatter(hsc_pixel_coverage['ra'], hsc_pixel_coverage['dec'], c=hsc_pixel_coverage['extent'])
ax1.set_xlabel('Right Ascension')
ax1.set_ylabel('Declination')
ax1.set_title('Pixel coverage for HSC')

ax2.scatter(delve_pixel_coverage['ra'], delve_pixel_coverage['dec'], c=delve_pixel_coverage['extent'])
ax2.set_xlabel('Right Ascension')
ax2.set_ylabel('Declination')
ax2.set_title('Pixel coverage for Delve')